In [1]:
# Step1: Load the data
import pandas as pd
import matplotlib.pyplot as plt

# Store file locations
file1_path = './Fuel_Level_Part_1-1.csv'
file2_path = './Fuel_Level_Part_2-1.csv'
file3_path = './Invoices-1.csv'
file4_path = './Locations-1.csv'
file5_path = './Tanks-1.csv'
# Load the CSV files
data1 = pd.read_csv(file1_path)
data2 = pd.read_csv(file2_path)
data_Invoices = pd.read_csv(file3_path)
data_Location = pd.read_csv(file4_path)
data_Tank = pd.read_csv(file5_path)

In [2]:
# Step2: Concate the 2 Fuel Level tables
# Standardlize the column names in two tables
data2.rename(columns={"Timestamp":"Time stamp"}, inplace=True)
data2.rename(columns={"Fuel_Level":"Fuel Level"}, inplace=True)

# Concatenate the two dataframes and make index unified
concatenated_data = pd.concat([data1, data2], ignore_index=True)

# Double-check the total number of rows
row_count_concatenated_data = concatenated_data.shape[0]
print(f"Total rows after concatenation: {row_count_concatenated_data}")

# Examine missing values
missing_fuel_level = concatenated_data["Fuel Level"].isnull().sum()
missing_time_stamp = concatenated_data["Time stamp"].isnull().sum()
print(f"Total missing values in 'Fuel Level': {missing_fuel_level}")
print(f"Total missing values in 'Time Stamp': {missing_time_stamp}")

# Handle the missing values in 'Fuel Level' column
concatenated_data["Fuel Level"] = concatenated_data["Fuel Level"].interpolate(method="polynomial", order=2)

# Display the first few rows of the concatenated dataframe to ensure success
import ace_tools_open as tools;
tools.display_dataframe_to_user(name="Concatenated Fuel Level Data", dataframe=concatenated_data)

Total rows after concatenation: 1859660
Total missing values in 'Fuel Level': 2
Total missing values in 'Time Stamp': 0
Concatenated Fuel Level Data


In [3]:
# Step3: Merge the Tank & Location table
# Standardlize the column names in two tables
data_Location.rename(columns={"Gas Station Location":"Tank Location"}, inplace=True)

# Merge the tables on 'Tank Location'
merged_tank_location = pd.merge(data_Tank, data_Location, on='Tank Location', how='inner')

# Display the merged data to verify success
tools.display_dataframe_to_user(name="Merged Tanks and Locations Data", dataframe=merged_tank_location)

# Double-check the total number of rows
row_count_merged_tank_location = merged_tank_location.shape[0]
print(f"Total rows after concatenation: {row_count_merged_tank_location}")

Merged Tanks and Locations Data


Total rows after concatenation: 23


In [4]:
# Step4: Merge the Tank_Location & Invoices table

# Standardlize the column names in two tables
data_Invoices.rename(columns={"Invoice Gas Station Location":"Tank Location"}, inplace=True)

# Merge the tables on 'Tank Location'
merged_tank_location_invoices = pd.merge(merged_tank_location, data_Invoices, on='Tank Location', how='inner')

# Drop rows with no invoices data
merged_tank_location_invoices.dropna(subset=['Gross Purchase Cost', 'Amount Purchased', 'Fuel Type'], inplace=True)

# Display the merged data to verify success
tools.display_dataframe_to_user(name="Merged Tanks, Locations, and Invoices Data", dataframe=merged_tank_location_invoices)

# Double-check the total number of rows
row_count_merged_tank_location_invoices = merged_tank_location_invoices.shape[0]
print(f"Total rows after concatenation: {row_count_merged_tank_location_invoices}")

Merged Tanks, Locations, and Invoices Data


Total rows after concatenation: 12412


In [5]:
# Step5: Visualise each tank's purchase patterns

# Ensure data is sorted by time for each tank
concatenated_data['Time stamp'] = pd.to_datetime(concatenated_data['Time stamp'])  # Convert to datetime
concatenated_data = concatenated_data.sort_values(by=['Tank ID', 'Time stamp'])

# Group data by 'Tank ID'
grouped_data = concatenated_data.groupby('Tank ID')

# Create subplots
num_tanks = len(grouped_data)
fig, axes = plt.subplots(num_tanks, 1, figsize=(50, 5 * num_tanks), sharex=True)

# Plot each tank's fuel level in its own subplot
for ax, (tank_id, tank_data) in zip(axes, grouped_data):
    ax.plot(tank_data['Time stamp'], tank_data['Fuel Level'], label=f'Tank {tank_id}')
    ax.set_title(f'Fuel Level Over Time - Tank {tank_id}', fontsize=14)
    ax.set_xlabel('Time', fontsize=12)
    ax.set_ylabel('Fuel Level', fontsize=12)
    ax.grid(True)
    ax.legend()

# Adjust layout for better spacing
plt.tight_layout()
plt.show() 


In [8]:
import plotly.express as px

# Create an interactive line plot with Plotly
fig = px.line(
    concatenated_data,
    x='Time stamp',
    y='Fuel Level',
    color='Tank ID',  # Optional: separate by tank ID
    title='Fuel Level Over Time',
    labels={'Time stamp': 'Time', 'Fuel Level': 'Fuel Level'},
)

# Customize layout
fig.update_layout(
    xaxis_title="Time",
    yaxis_title="Fuel Level",
    hovermode="x unified",
    template="plotly_white"
)

fig.show()


ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

In [ ]:
# Step6: Quantify Current Performance

# Filter for stations 1–8
stations_1_to_8 = merged_tank_location_invoices[merged_tank_location_invoices['Tank Location'].isin(range(1, 9))]

# Define a function to calculate discounts based on purchase quantity
def calculate_discount(order_amount):
    if order_amount > 40000:
        return 4  # cents per liter
    elif order_amount > 25000:
        return 3
    elif order_amount > 15000:
        return 2
    else:
        return 0

# Calculate discount per liter and cost savings
stations_1_to_8['Discount Per Liter'] = stations_1_to_8['Amount Purchased'].apply(calculate_discount)
stations_1_to_8['Cost Savings'] = (stations_1_to_8['Amount Purchased'] * stations_1_to_8['Discount Per Liter']) / 100  # Convert to dollars

# Summarize total gross cost and cost savings
summary = stations_1_to_8.groupby('Tank Location').agg(
    Total_Gross_Cost=('Gross Purchase Cost', 'sum'),
    Total_Cost_Savings=('Cost Savings', 'sum')
).reset_index()

# Calculate Total Net Cost separately
summary['Total_Net_Cost'] = summary['Total_Gross_Cost'] - summary['Total_Cost_Savings']

# Display the current performance summary
tools.display_dataframe_to_user(name="Current Cost Savings for Stations 1-8", dataframe=summary)


Cost Savings for Stations 1-8


In [ ]:
# Step7: Determine Highest Applicable Discount Rate

# Group by Tank Location and Fuel Type
fuel_capacity_by_location = data_Tank.groupby(['Tank Location', 'Tank Type']).agg(
    Total_Tank_Capacity=('Tank Capacity', 'sum')  # Sum the tank capacities for each fuel type at each location
).reset_index()

# Function to determine the highest applicable discount rate
def calculate_highest_discount_rate(tank_capacity):
    if tank_capacity > 40000:
        return 4  # cents per liter
    elif tank_capacity > 25000:
        return 3
    elif tank_capacity > 15000:
        return 2
    else:
        return 0

# Calculate the highest applicable discount rate for each group
fuel_capacity_by_location['Highest_Discount_Rate (cent/Liter)'] = fuel_capacity_by_location['Total_Tank_Capacity'].apply(calculate_highest_discount_rate)

# Display the results
tools.display_dataframe_to_user(name="Total Tank Capacity by Fuel Type and Location", dataframe=fuel_capacity_by_location)


Total Tank Capacity by Fuel Type and Location


In [ ]:
# Step8: Calculate 7-Day Inventory Threshold

# Calculate daily consumption for each tank
concatenated_data['Daily Consumption'] = concatenated_data.groupby('Tank ID')['Fuel Level'].diff().abs()

# Drop NaN values caused by diff()
concatenated_data = concatenated_data.dropna(subset=['Daily Consumption'])

# Extract date from timestamp
concatenated_data['Date'] = concatenated_data['Time stamp'].dt.date

# Merge with Tanks data to associate Tank Location and Fuel Type
merged_data = pd.merge(
    concatenated_data,
    tanks[['Tank ID', 'Tank Location', 'Fuel Type']],
    on='Tank ID',
    how='left'
)

# Group by Tank Location, Fuel Type, and Date to calculate daily consumption
daily_consumption = merged_data.groupby(['Tank Location', 'Fuel Type', 'Date']).agg(
    Daily_Consumption=('Daily Consumption', 'sum')
).reset_index()

# Calculate the average daily consumption for each location and fuel type
average_daily_consumption = daily_consumption.groupby(['Tank Location', 'Fuel Type']).agg(
    Average_Daily_Consumption=('Daily_Consumption', 'mean')
).reset_index()

# Display the results
tools.display_dataframe_to_user(name="Average Daily Consumption by Location and Fuel Type", dataframe=average_daily_consumption)


NameError: name 'tanks' is not defined

In [ ]:
# Step8: Calculate a 7-day inventory threshold

# Convert the timestamp to date (for calculation purpose)
concatenated_data['Date'] = concatenated_data['Time stamp'].dt.date

# Calculate differences in fuel level
concatenated_data['Fuel Level Change'] = concatenated_data.groupby('Tank ID')['Fuel Level'].diff()

# Keep only negative changes (consumption) and set positive changes to 0
concatenated_data['Fuel Level Change'] = concatenated_data['Fuel Level Change'].where(
    concatenated_data['Fuel Level Change'] < 0, 0
).abs()

# Group by Tank ID and Date to sum the daily consumption
daily_consumption = concatenated_data.groupby(['Tank ID', 'Date']).agg(
    Daily_Consumption=('Fuel Level Change', 'sum')
).reset_index()

# Display the results
tools.display_dataframe_to_user(name="Daily Consumption by Tank and Date", dataframe=daily_consumption)


KeyError: 'Tank Location'